## I. EDA

#### Importing libraries and data from Kaggle

In [ ]:
!pip install -q folium
!pip install -q keplergl
!pip install -q opendatasets
!pip install -q reverse_geocoder
!pip install -q pycountry
!pip install -q pycaret

username : harshiniaiyyer
pwd: db9694435b6d0b386a9c18289bb0f443

In [ ]:
import opendatasets as od
od.download('https://www.kaggle.com/datasets/jaypanderson/cleaned-meteorite-data/data')

Please provide your Kaggle credentials to download this dataset. Learn more: http://bit.ly/kaggle-creds
Your Kaggle username: harshiniaiyyer
Your Kaggle Key: ··········
Dataset URL: https://www.kaggle.com/datasets/jaypanderson/cleaned-meteorite-data


100%|██████████| 1.34M/1.34M [00:00<00:00, 1.76MB/s]

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import folium as fo
from keplergl import KeplerGl

In [ ]:
df1 = pd.read_csv('/content/cleaned-meteorite-data/cleaned_meteorite_data.csv')
df1.head()

Unnamed: 0      name   id name_type    rec_class      mass  fall    year  \
0           0    Aachen    1     Valid           L5      21.0  Fell  1880.0   
1           1    Aarhus    2     Valid           H6     720.0  Fell  1951.0   
2           2      Abee    6     Valid          EH4  107000.0  Fell  1952.0   
3           3  Acapulco   10     Valid  Acapulcoite    1914.0  Fell  1976.0   
4           4   Achiras  370     Valid           L6     780.0  Fell  1902.0   

    rec_lat   rec_long geo_location location_type  
0  50.77500    6.08333          NaN         Exact  
1  56.18333   10.23333          NaN         Exact  
2  54.21667 -113.00000          NaN         Exact  
3  16.88333  -99.90000          NaN         Exact  
4 -33.16667  -64.95000          NaN         Exact

In [ ]:
import reverse_geocoder as rg

re = rg.search((50.77500, 6.08333))
res = re[0]['cc']

Loading formatted geocoded file...


In [ ]:
import pycountry as pc

country_name = pc.countries.get(alpha_2=res).name
print(f"The country is: {country_name}")

The country is: Germany


### Data Cleaning (ende thalai ezhuthu)

In [ ]:
df1 = df1[0:1500]
df1.shape

(1500, 12)

In [ ]:
df1 = df1.drop([df1.columns[0],'id','geo_location'], axis=1)
df1.head()

name name_type    rec_class      mass  fall    year   rec_lat  \
0    Aachen     Valid           L5      21.0  Fell  1880.0  50.77500   
1    Aarhus     Valid           H6     720.0  Fell  1951.0  56.18333   
2      Abee     Valid          EH4  107000.0  Fell  1952.0  54.21667   
3  Acapulco     Valid  Acapulcoite    1914.0  Fell  1976.0  16.88333   
4   Achiras     Valid           L6     780.0  Fell  1902.0 -33.16667   

    rec_long location_type  
0    6.08333         Exact  
1   10.23333         Exact  
2 -113.00000         Exact  
3  -99.90000         Exact  
4  -64.95000         Exact

In [ ]:
df1.isnull().sum()

name              0
name_type         0
rec_class         0
mass             32
fall              0
year              1
rec_lat          10
rec_long         10
location_type     0
dtype: int64

In [ ]:
df = df1.dropna()
df.head()

name name_type    rec_class      mass  fall    year   rec_lat  \
0    Aachen     Valid           L5      21.0  Fell  1880.0  50.77500   
1    Aarhus     Valid           H6     720.0  Fell  1951.0  56.18333   
2      Abee     Valid          EH4  107000.0  Fell  1952.0  54.21667   
3  Acapulco     Valid  Acapulcoite    1914.0  Fell  1976.0  16.88333   
4   Achiras     Valid           L6     780.0  Fell  1902.0 -33.16667   

    rec_long location_type  
0    6.08333         Exact  
1   10.23333         Exact  
2 -113.00000         Exact  
3  -99.90000         Exact  
4  -64.95000         Exact

### Getting the country and adding to the name of the province


In [ ]:
import reverse_geocoder as rg
import pycountry as pc

# Assuming df is your DataFrame with 'rec_lat' and 'rec_long' columns
country = []
for i,j in zip(df['rec_lat'],df['rec_long']):
  re = rg.search((i, j))
  res = re[0]['cc']
  country_name = pc.countries.get(alpha_2=res).name
  country.append(country_name)

In [ ]:
df['country'] = country
df['exactloc'] = df['name'] + ', ' + df['country']
df.head()

<ipython-input-13-f54ea19c718c>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['country'] = country
<ipython-input-13-f54ea19c718c>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['exactloc'] = df['name'] + ', ' + df['country']


name name_type    rec_class      mass  fall    year   rec_lat  \
0    Aachen     Valid           L5      21.0  Fell  1880.0  50.77500   
1    Aarhus     Valid           H6     720.0  Fell  1951.0  56.18333   
2      Abee     Valid          EH4  107000.0  Fell  1952.0  54.21667   
3  Acapulco     Valid  Acapulcoite    1914.0  Fell  1976.0  16.88333   
4   Achiras     Valid           L6     780.0  Fell  1902.0 -33.16667   

    rec_long location_type    country            exactloc  
0    6.08333         Exact    Germany     Aachen, Germany  
1   10.23333         Exact    Denmark     Aarhus, Denmark  
2 -113.00000         Exact     Canada        Abee, Canada  
3  -99.90000         Exact     Mexico    Acapulco, Mexico  
4  -64.95000         Exact  Argentina  Achiras, Argentina

## II.  Folium Viz

#### The usual Folium map

In [ ]:
latitude = 50.77500
longitude = 6.08333
maps = fo.Map(location=[0,0], zoom_start=4)

In [ ]:
met = fo.map.FeatureGroup()

for i,j,k in zip(df['rec_lat'],df['rec_long'],df['name']):
  fo.CircleMarker(
      location = [i,j],
      radius = 0.5,
      color = 'red',
      fill = False,
      popup = k
  ).add_to(met)

maps.add_child(met)

#### Clustered maps

In [ ]:
from folium import plugins

la = 0.00000
lo = 0.00000
maps1 = fo.Map(location=[la, lo], zoom_start=4)

metcluster = fo.plugins.MarkerCluster().add_to(maps1)

for i,j,k in zip(df['rec_lat'],df['rec_long'],df['name']):
  fo.Marker(
      location = [i,j],
      popup = k
  ).add_to(metcluster)

maps1.add_child(metcluster)

In [ ]:
from sklearn.preprocessing import MinMaxScaler

# 1. Normalize the 'mass' values
scaler = MinMaxScaler()
df['mass'] = scaler.fit_transform(df[['mass']])

<ipython-input-17-6a2e4f1aba78>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['mass'] = scaler.fit_transform(df[['mass']])


### Heatmaps based on the mass of falling meteorite

In [ ]:
from folium.plugins import HeatMap

hmaps = fo.Map(location=[la, lo], zoom_start=4)

heat = [[row['rec_lat'], row['rec_long'], row['mass']] for index, row in df.iterrows()]

HeatMap(heat).add_to(hmaps)

#Add a custom legend
leg = '''
<div style="position: fixed;
    bottom: 50px; left: 50px; width: 150px; height: 150px;
    background-color: white; border:2px solid grey; z-index:9999; font-size:14px; padding: 10px;">
    <b>Heatmap Legend</b><br>
    <i style="background: blue; width: 20px; height: 20px; display: inline-block; margin-right: 5px;"></i> Low Mass<br>
    <i style="background: green; width: 20px; height: 20px; display: inline-block; margin-right: 5px;"></i> Medium Mass<br>
    <i style="background: yellow; width: 20px; height: 20px; display: inline-block; margin-right: 5px;"></i> High Mass<br>
    <i style="background: red; width: 20px; height: 20px; display: inline-block; margin-right: 5px;"></i> Very High Mass
</div>
'''

hmaps.get_root().html.add_child(fo.Element(leg))

hmaps

## III. ML


In [ ]:
x = df[['name_type','mass','rec_lat','rec_long','location_type']]
y = df[['fall']]

In [ ]:
# Import necessary libraries
from pycaret.classification import *

# Initialize the setup
# 'target' is the name of the target column in your df dataset
clf = setup(data=df, target=df['fall'], session_id=123)

In [ ]:
# Compare models to see which performs best
best_model = compare_models()
best_model

Processing:   0%|          | 0/65 [00:00<?, ?it/s]

GaussianNB(priors=None, var_smoothing=1e-09)

mlp -> 0.9912
decision tree + other ensemble models -> 0.73
over 38% increase